In [ ]:
def Compute_IVX_Wald(y, X, K, M_n, beta):
    #y=r
    #X=-SII
    #K=h[j]
    #M_n=0
    #beta=0.99

    X_lagged = X[:-1]
    X_constant = np.ones((len(y)-1, 1))
    X_combined = np.concatenate((X_constant, X_lagged), axis=1)

    results_OLS_y = sm.OLS(y[1:], X_combined).fit()
    epsilon_hat = results_OLS_y.resid.reshape(-1, 1)
    U_hat = np.empty((len(y)-1, X.shape[1]))
    U_hat[:] = np.nan


    for j in range(X.shape[1]):
        results_OLS_j = sm.OLS(X[1:, j], X_combined).fit()
        U_hat[:, j] = results_OLS_j.resid

    Sigma_hat_ee = (1/len(epsilon_hat)) * np.dot(epsilon_hat.T, epsilon_hat)
    Sigma_hat_eu = (1/len(epsilon_hat)) * np.dot(epsilon_hat.T, U_hat)
    Sigma_hat_uu = (1/len(epsilon_hat)) * np.dot(U_hat.T, U_hat)
    Omega_hat_uu = Sigma_hat_uu
    Omega_hat_eu = Sigma_hat_eu

    if M_n > 0:
        Lambda_hat_uu = np.zeros((U_hat.shape[1], U_hat.shape[1]))
        Lambda_hat_ue = np.zeros((U_hat.shape[1], 1))
        for h in range(1, M_n+1):
            Lambda_hat_uu += (1 - (h / (M_n + 1))) * (1 / (len(U_hat) - 1)) * np.dot(U_hat[h:, :].T, U_hat[:-h, :])
            Lambda_hat_ue += (1 - (h / (M_n + 1))) * (1 / (len(U_hat) - 1)) * np.dot(U_hat[h:, :].T, epsilon_hat[:-h, :])
        Omega_hat_uu = Sigma_hat_uu + Lambda_hat_uu + Lambda_hat_uu.T
        Omega_hat_eu = Sigma_hat_eu + Lambda_hat_ue.T

    R_nz = 1 - (1 / (len(y) - 1) ** beta)
    d_X = np.diff(X, axis=0)
    d_X = np.vstack([np.zeros((1, d_X.shape[1])), d_X])
    Z_tilde = np.full((X.shape[0], X.shape[1]), np.nan)
    Z_tilde[0, :] = np.zeros(X.shape[1])

    for t in range(1, X.shape[0]):
        Z_tilde[t, :] = R_nz * Z_tilde[t-1, :] + d_X[t, :]

    y_K = np.full((len(y) - (K-1), 1), np.nan)
    X_K = np.full((len(y) - (K-1), X.shape[1]), np.nan)
    Z_tilde_K = np.full((len(y) - (K-1), X.shape[1]), np.nan)

    for t in range(len(y) - (K-1)):
        y_K[t] = np.sum(y[t:t+K])
        X_K[t,:] = np.sum(X[t:t+K,:], axis=0)
        Z_tilde_K[t,:] = np.sum(Z_tilde[t:t+K,:], axis=0)

    n_K = len(y_K) - 1
    y_bar_K = np.mean(y_K[1:])
    x_bar_K = np.mean(X_K[:-1, :], axis=0)
    z_tilde_bar_K = np.mean(Z_tilde_K[:-K, :], axis=0)
    Y_K_under = y_K[1:] - y_bar_K
    X_K_under = X_K[:-1, :] - np.kron(x_bar_K.reshape(-1, 1), np.ones((n_K, 1)))
    Z_tilde_K = Z_tilde_K[:-K, :]
    Z_tilde = Z_tilde[:-K, :]  

    A_tilde_IVX_K = np.linalg.inv(X_K_under.T @ Z_tilde) @ (Z_tilde.T @ Y_K_under)
    Omega_hat_FM = Sigma_hat_ee - Omega_hat_eu @ np.linalg.inv(Omega_hat_uu) @ Omega_hat_eu.T
    M_K = (Z_tilde_K.T @ Z_tilde_K) @ Sigma_hat_ee - n_K * np.outer(z_tilde_bar_K, z_tilde_bar_K) @ Omega_hat_FM
    Q_H_K = np.linalg.inv(Z_tilde.T @ X_K_under) @ M_K @ np.linalg.inv(X_K_under.T @ Z_tilde)
    W_IVX_K = A_tilde_IVX_K.T @ np.linalg.inv(Q_H_K) @ A_tilde_IVX_K
    p_value = 1 - stats.chi2.cdf(W_IVX_K, X.shape[1])
    return A_tilde_IVX_K, W_IVX_K, p_value

In [ ]:
def Compute_qLL_hat(y, X, Z, L):
   

    T, k = X.shape

    XZ = np.concatenate((X, Z), axis=1)
    results = sm.OLS(y, XZ).fit()
    epsilon_hat = results.resid.reshape(-1, 1)

    X_epsilon_hat = X * np.kron(np.ones((1, k)), epsilon_hat)
    V_hat_X = (1/T) * X_epsilon_hat.T @ X_epsilon_hat

    if L >= 1:
        for l in range(1, L+1):
            Gamma_hat_l = (1/T) * (X_epsilon_hat[l:, :].T @ X_epsilon_hat[:-(l), :])

            V_hat_X += (1 - (l/(L+1))) * (Gamma_hat_l + Gamma_hat_l.T)


    U_hat = np.linalg.inv(np.sqrt(V_hat_X)) @ X_epsilon_hat.T

    r_bar = 1 - (10 / T)
    w_hat = np.zeros((k, T))

    for t in range(T):
        if t == 0:
            w_hat[:, t] = U_hat[:, t]
        else:
            w_hat[:, t] = r_bar * w_hat[:, t-1] + (U_hat[:, t] - U_hat[:, t-1])


    r_bar_trend = r_bar**(np.arange(1, len(y)+1)).reshape(-1, 1)
    SSR = np.empty((k, 1))
    SSR[:] = np.nan

    for i in range(k):
        model = sm.OLS(w_hat[i, :], r_bar_trend)
        results_i = model.fit()
        SSR[i] = np.dot(results_i.resid.T, results_i.resid)

    qLL_hat = r_bar * np.sum(SSR) - np.sum(np.sum(U_hat**2, axis=1))
    return qLL_hat


